<a href="https://colab.research.google.com/gist/adamsilverstein/20fbb28b6db2c280089b79b9fadb2ca1/wpp-metrics-tracking.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# WPP Tracking

Track CWV metric pass rate and feature adoption metrics across initiatives.

# Setup

In [ ]:
project_id = 'wpp-research'

### Provide your credentials to the runtime

In [ ]:
from google.colab import auth
auth.authenticate_user()
print('Authenticated')


Authenticated


### Declare the Cloud project ID which will be used throughout this notebook



In [ ]:
from google.cloud.bigquery import magics
# Update with your own Google Cloud Platform project name
magics.context.project = project_id

### Add a helper to get the latest dataset

In [ ]:
from datetime import datetime, timedelta

def get_first_of_previous_month():
    today = datetime.now()
    first_day_previous_month = datetime(today.year, today.month - 1, 1) if today.month > 1 else datetime(today.year - 1, 12, 1)
    return first_day_previous_month.strftime('%Y_%m_%d')

latest_dataset = get_first_of_previous_month() # eg. "2023_06_01" - datasets are updated monthly, indicate the latest

### Enable data table display

In [ ]:
%load_ext google.colab.data_table

In [ ]:
from google.colab import data_table
data_table.enable_dataframe_formatter()

# Helper Functions

Define helper functions that are used repeatedly throughout the colab.

`query_cwv_for_technology_over_dates` - Calculate CWV metrics over time for technology


### Helper to show CWV metrics over time for technology

In [ ]:
from google.cloud import bigquery
from datetime import datetime, timedelta

client = bigquery.Client(project=project_id)

def query_cwv_for_technology_over_dates(technology, from_date=None, to_date=None):
  """
    Queries Core Web Vitals metrics from HTTP Archive for a specific technology
    over the past 12 months.

    Args:
        technology (str): The technology to filter by (e.g., 'React').
        from_date (str, optional): The start date in YYYY_MM_DD format.
        to_date (str, optional): The end date in YYYY_MM_DD format.
    Returns:
        A BigQuery query result object containing CWV data.
  """
  # set to_date if not passed
  if not to_date:
    to_date = latest_dataset

  # set from date if not passed
  if not from_date:
    from_date = (datetime.strptime(to_date, '%Y_%m_%d').date() - timedelta(days=365)).strftime('%Y_%m_%d')


  query = f"""
CREATE TEMP FUNCTION IS_GOOD(good FLOAT64, needs_improvement FLOAT64, poor FLOAT64)
    RETURNS BOOL
    AS (
      good / (good + needs_improvement + poor) >= 0.75
    );

    CREATE TEMP FUNCTION IS_NON_ZERO(good FLOAT64, needs_improvement FLOAT64, poor FLOAT64)
    RETURNS BOOL
    AS (
      good + needs_improvement + poor > 0
    );
  WITH sites_using_technology AS (
    SELECT
      page AS origin,
      client AS device,
      date,
    FROM
      `httparchive.all.pages`,
      UNNEST(technologies) AS technologies
    WHERE
      technologies.technology = '{technology}'
      AND date BETWEEN PARSE_DATE('%Y_%m_%d', '{from_date}') AND PARSE_DATE('%Y_%m_%d', '{to_date}' )
      AND is_root_page = TRUE
    GROUP BY
      page, device, date
  ),
  cwv_metrics_for_origins AS (
    SELECT
      cwvs.date AS date,
      sites_using_technology.origin AS origin,
      # Device phone or tablet as mobile, otherwise desktop.
      IF(cwvs.device = 'phone' OR cwvs.device = 'tablet', 'mobile', 'desktop') AS device,
      IS_NON_ZERO(fast_inp, avg_inp, slow_inp) AS any_inp,
      IS_GOOD(fast_inp, avg_inp, slow_inp) AS good_inp,
      IS_NON_ZERO(small_cls, medium_cls, large_cls) AS any_cls,
      IS_GOOD(small_cls, medium_cls, large_cls) AS good_cls,
      IS_NON_ZERO(fast_lcp, avg_lcp, slow_lcp) AS any_lcp,
      IS_GOOD(fast_lcp, avg_lcp, slow_lcp) AS good_lcp,
      (IS_GOOD(fast_inp, avg_inp, slow_inp) OR fast_inp IS NULL) AND IS_GOOD(small_cls, medium_cls, large_cls) AND IS_GOOD(fast_lcp, avg_lcp, slow_lcp) AS good_cwv
    FROM
      `chrome-ux-report.materialized.device_summary` AS cwvs
     JOIN
      sites_using_technology
    ON (
      sites_using_technology.origin = CONCAT(cwvs.origin, '/') AND
      sites_using_technology.date   = cwvs.date AND
      sites_using_technology.device = IF(cwvs.device = 'phone' OR cwvs.device = 'tablet', 'mobile', cwvs.device)
    )
    WHERE
      cwvs.date BETWEEN PARSE_DATE('%Y_%m_%d', '{from_date}') AND PARSE_DATE('%Y_%m_%d', '{to_date}' )
      AND cwvs.device IN ('desktop', 'tablet', 'phone')

  ),


  cwvs_by_date AS (
    SELECT
      date,
      device,
      COUNT(DISTINCT origin) AS origins,
      SAFE_DIVIDE(COUNTIF(good_cwv), COUNTIF(any_lcp AND any_cls)) AS pct_eligible_origins_with_good_cwv,
      SAFE_DIVIDE(COUNTIF(good_lcp), COUNTIF(any_lcp)) AS pct_eligible_origins_with_good_lcp,
      SAFE_DIVIDE(COUNTIF(good_cls), COUNTIF(any_cls)) AS pct_eligible_origins_with_good_cls,
      SAFE_DIVIDE(COUNTIF(good_inp), COUNTIF(any_inp)) AS pct_eligible_origins_with_good_inp
    FROM
      cwv_metrics_for_origins
    GROUP BY
      date, device
    ORDER BY
      date, device
    )
  SELECT * FROM cwvs_by_date
  """

  query_job = client.query(query)
  return query_job.result()  # Return the results of the query

# Restrict the query to on the from and to dates, and to the specified from and to versions
def query_cwv_for_technology_compare_dates_by_version(technology, from_date, to_date, from_version, to_version):
  """
    Queries Core Web Vitals metrics from HTTP Archive for a specific technology
    over the past 12 months.

    Args:
        technology (str): The technology to filter by (e.g., 'React').
        from_date (str): The start date in YYYY_MM_DD format.
        to_date (str): The end date in YYYY_MM_DD format.
        from_version (str): The start version.
        to_version (str): The end version.
    Returns:
        A BigQuery query result object containing CWV data.
  """
  # set to_date if not passed
  if not to_date:
    to_date = latest_dataset

  # set from date if not passed
  if not from_date:
    from_date = (datetime.strptime(to_date, '%Y_%m_%d').date() - timedelta(days=365)).strftime('%Y_%m_%d')


  query = f"""
CREATE TEMP FUNCTION IS_GOOD(good FLOAT64, needs_improvement FLOAT64, poor FLOAT64)
    RETURNS BOOL
    AS (
      good / (good + needs_improvement + poor) >= 0.75
    );

    CREATE TEMP FUNCTION IS_NON_ZERO(good FLOAT64, needs_improvement FLOAT64, poor FLOAT64)
    RETURNS BOOL
    AS (
      good + needs_improvement + poor > 0
    );
  WITH sites_using_technology AS (
    SELECT
      page AS origin,
      client AS device,
      date,
    FROM
      `httparchive.all.pages`,
      UNNEST(technologies) AS technologies
    WHERE
      technologies.technology = '{technology}'
      AND (
        ( date = PARSE_DATE('%Y_%m_%d', '{from_date}') AND REGEXP_EXTRACT(JSON_EXTRACT( JSON_EXTRACT(payload, '$._detected_apps'),'$.{technology}'),r'(\\d.\\d+.\\d+).*') = '{from_version}' ) OR
        ( date = PARSE_DATE('%Y_%m_%d', '{to_date}' ) AND REGEXP_EXTRACT(JSON_EXTRACT( JSON_EXTRACT(payload, '$._detected_apps'),'$.{technology}'),r'(\\d.\\d+.\\d+).*') = '{to_version}' )
      )
      AND is_root_page = TRUE
    GROUP BY
      page, device, date
  ),
  cwv_metrics_for_origins AS (
    SELECT
      cwvs.date AS date,
      sites_using_technology.origin AS origin,
      # Device phone or tablet as mobile, otherwise desktop.
      IF(cwvs.device = 'phone' OR cwvs.device = 'tablet', 'mobile', cwvs.device) AS device,
      IS_NON_ZERO(fast_inp, avg_inp, slow_inp) AS any_inp,
      IS_GOOD(fast_inp, avg_inp, slow_inp) AS good_inp,
      IS_NON_ZERO(small_cls, medium_cls, large_cls) AS any_cls,
      IS_GOOD(small_cls, medium_cls, large_cls) AS good_cls,
      IS_NON_ZERO(fast_lcp, avg_lcp, slow_lcp) AS any_lcp,
      IS_GOOD(fast_lcp, avg_lcp, slow_lcp) AS good_lcp,
      (IS_GOOD(fast_inp, avg_inp, slow_inp) OR fast_inp IS NULL) AND IS_GOOD(small_cls, medium_cls, large_cls) AND IS_GOOD(fast_lcp, avg_lcp, slow_lcp) AS good_cwv
    FROM
      `chrome-ux-report.materialized.device_summary` AS cwvs
     JOIN
      sites_using_technology
    ON (
      sites_using_technology.origin = CONCAT(cwvs.origin, '/') AND
      sites_using_technology.date   = cwvs.date AND
      sites_using_technology.device = IF(cwvs.device = 'phone' OR cwvs.device = 'tablet', 'mobile', cwvs.device)
    )
    WHERE
      cwvs.date BETWEEN PARSE_DATE('%Y_%m_%d', '{from_date}') AND PARSE_DATE('%Y_%m_%d', '{to_date}' )
      AND cwvs.device IN ('desktop', 'tablet', 'phone')
      # Restrict to sites that are in both dates
      AND CONCAT(cwvs.origin, '/') IN (
        SELECT
          origin
        FROM
          sites_using_technology
        GROUP BY
          origin
        HAVING
          COUNT(*) = 2
      )
  ),


  cwvs_by_date AS (
    SELECT
      date,
      device,
      COUNT(DISTINCT origin) AS origins,
      SAFE_DIVIDE(COUNTIF(good_cwv), COUNTIF(any_lcp AND any_cls)) AS pct_eligible_origins_with_good_cwv,
      SAFE_DIVIDE(COUNTIF(good_lcp), COUNTIF(any_lcp)) AS pct_eligible_origins_with_good_lcp,
      SAFE_DIVIDE(COUNTIF(good_cls), COUNTIF(any_cls)) AS pct_eligible_origins_with_good_cls,
      SAFE_DIVIDE(COUNTIF(good_inp), COUNTIF(any_inp)) AS pct_eligible_origins_with_good_inp
    FROM
      cwv_metrics_for_origins
    GROUP BY
      date, device
    ORDER BY
      date, device
    )
  SELECT * FROM cwvs_by_date
  """

  query_job = client.query(query)
  return query_job.result()  # Return the results of the query

## Feature performance analysis helpers

In [ ]:
#@markdown ## Get sites at `after_date` with feature active.
from google.cloud import bigquery
import pandas as pd

# This limit is used throughout, adjust to increase sample or speed.
limit = 50000


# Get sites with the feature active on a specific date
def get_sites_with_feature_active(generator_tag, after_date):
  client = bigquery.Client(project=project_id)
  # 1. Identify Active and Non-Active Sites
  active_sites_query = f"""
    CREATE TEMP FUNCTION getFeature(payload STRING, generator_tag STRING)
    RETURNS STRING
    LANGUAGE js
    AS '''
      try {{
        var $ = JSON.parse(payload);
        var almanac = JSON.parse($._almanac);
        var generators = almanac['meta-nodes'].nodes.find(node => node.name == 'generator' && node.content.startsWith(generator_tag));
        if ( generators.length == 0 ) {{
          return "";
        }}
        var content =  generators.content;
        return content;
      }} catch (e) {{
        return "";
      }}
    ''';


    SELECT
      page AS origin
    FROM
      `httparchive.all.pages`,
      UNNEST(technologies) AS technologies
    WHERE
      technologies.technology = 'WordPress'
      AND date = PARSE_DATE('%Y-%m-%d', '{after_date}' )
      AND is_root_page = TRUE
      AND client = 'mobile'
      AND getFeature(payload, '{generator_tag}') != ""


    LIMIT {limit}
  """

  active_sites_df = client.query(active_sites_query).to_dataframe()
  return active_sites_df

### Get sites with features active

In [ ]:
#@markdown ## Get sites at `after_date` with feature active.
from google.cloud import bigquery
import pandas as pd

# This limit is used throughout, adjust to increase sample or speed.
limit = 50000


# Get sites with the feature active on a specific date
def get_sites_with_features_active(generator_tag1, generator_tag2, after_date):
  client = bigquery.Client(project=project_id)
  # 1. Identify Active and Non-Active Sites
  active_sites_query = f"""
    CREATE TEMP FUNCTION getFeature(payload STRING, generator_tag STRING)
    RETURNS STRING
    LANGUAGE js
    AS '''
      try {{
        var $ = JSON.parse(payload);
        var almanac = JSON.parse($._almanac);
        var generators = almanac['meta-nodes'].nodes.find(node => node.name == 'generator' && node.content.startsWith(generator_tag));
        if ( generators.length == 0 ) {{
          return "";
        }}
        var content =  generators.content;
        return content;
      }} catch (e) {{
        return "";
      }}
    ''';


    SELECT
      page AS origin
    FROM
      `httparchive.all.pages`,
      UNNEST(technologies) AS technologies
    WHERE
      technologies.technology = 'WordPress'
      AND date = PARSE_DATE('%Y-%m-%d', '{after_date}' )
      AND is_root_page = TRUE
      AND client = 'mobile'
      AND getFeature(payload, '{generator_tag1}') != ""
      AND getFeature(payload, '{generator_tag2}') != ""


    LIMIT {limit}
  """

  active_sites_df = client.query(active_sites_query).to_dataframe()
  return active_sites_df

In [ ]:
#@markdown ## Get sites at `after_date` with feature *not* active.
from google.cloud import bigquery
import pandas as pd


# Get sites with the feature active on a specific date
def get_sites_with_feature_inactive(generator_tag, after_date):
  client = bigquery.Client(project=project_id)
  # 1. Identify Active and Non-Active Sites
  inactive_sites_query = f"""
    CREATE TEMP FUNCTION getFeature(payload STRING, generator_tag STRING)
    RETURNS STRING
    LANGUAGE js
    AS '''
      try {{
        var $ = JSON.parse(payload);
        var almanac = JSON.parse($._almanac);
        var generators = almanac['meta-nodes'].nodes.find(node => node.name == 'generator' && node.content.startsWith(generator_tag));
        if ( generators.length == 0 ) {{
          return "";
        }}
        var content =  generators.content;
        return content;
      }} catch (e) {{
        return "";
      }}
    ''';


    SELECT
      page AS origin
    FROM
      `httparchive.all.pages`,
      UNNEST(technologies) AS technologies
    WHERE
      technologies.technology = 'WordPress'
      AND date = PARSE_DATE('%Y-%m-%d', '{after_date}' )
      AND is_root_page = TRUE
      AND client = 'mobile'
      AND getFeature(payload, '{generator_tag}') = ""


    LIMIT {limit}
  """

  inactive_sites_df = client.query(inactive_sites_query).to_dataframe()
  return inactive_sites_df

In [ ]:
#@markdown ## Get sites at `after_date` with feature *not* active.
from google.cloud import bigquery
import pandas as pd


# Get sites with the feature active on a specific date
def get_sites_with_features_inactive(generator_tag1, generator_tag2, after_date):
  client = bigquery.Client(project=project_id)
  # 1. Identify Active and Non-Active Sites
  inactive_sites_query = f"""
    CREATE TEMP FUNCTION getFeature(payload STRING, generator_tag STRING)
    RETURNS STRING
    LANGUAGE js
    AS '''
      try {{
        var $ = JSON.parse(payload);
        var almanac = JSON.parse($._almanac);
        var generators = almanac['meta-nodes'].nodes.find(node => node.name == 'generator' && node.content.startsWith(generator_tag));
        if ( generators.length == 0 ) {{
          return "";
        }}
        var content =  generators.content;
        return content;
      }} catch (e) {{
        return "";
      }}
    ''';


    SELECT
      page AS origin
    FROM
      `httparchive.all.pages`,
      UNNEST(technologies) AS technologies
    WHERE
      technologies.technology = 'WordPress'
      AND date = PARSE_DATE('%Y-%m-%d', '{after_date}' )
      AND is_root_page = TRUE
      AND client = 'mobile'
      AND getFeature(payload, '{generator_tag1}') = ""
      AND getFeature(payload, '{generator_tag2}') = ""


    LIMIT {limit}
  """

  inactive_sites_df = client.query(inactive_sites_query).to_dataframe()
  return inactive_sites_df

## Helpers to compare before and after, minus baseline

In [ ]:
#@markdown ## Get sites at `before_date` with feature active.
#@markdown Ideally, this should be 0.

# Calculate how many of the sites where the feature was active at the after_date
# did not have the feature active at the before_date
from google.cloud import bigquery
import pandas as pd


# Get sites from a list with the feature not active on a specific date
def get_active_sites_also_active_at_before_date(generator_tag, before_date, existing_sites):
  client = bigquery.Client(project=project_id)

  # Extract the origins from the existing_sites dataframe as a comma separated list
  existing_sites_list = ', '.join(f"'{origin}'" for origin in existing_sites['origin'])


  # 1. Identify Active and Non-Active Sites
  active_sites_query = f"""
    CREATE TEMP FUNCTION getFeature(payload STRING, generator_tag STRING)
    RETURNS STRING
    LANGUAGE js
    AS '''
      try {{
        var $ = JSON.parse(payload);
        var almanac = JSON.parse($._almanac);
        var generators = almanac['meta-nodes'].nodes.find(node => node.name == 'generator' && node.content.startsWith(generator_tag));
        if ( generators.length == 0 ) {{
          return "";
        }}
        var content =  generators.content;
        return content;
      }} catch (e) {{
        return "";
      }}
    ''';


    SELECT
      page AS origin
    FROM
      `httparchive.all.pages`,
       UNNEST(technologies) AS technologies

    WHERE
      technologies.technology = 'WordPress'
      AND date = PARSE_DATE('%Y-%m-%d', '{before_date}' )
      AND is_root_page = TRUE
      AND client = 'mobile'
      AND page IN ({existing_sites_list})
      AND getFeature(payload, '{generator_tag}') != ""
    LIMIT {limit}
  """

  active_sites_df = client.query(active_sites_query).to_dataframe()
  return active_sites_df

In [ ]:
#@markdown ## Get sites at `before_date` with feature active.
#@markdown Ideally, this should be 0.

# Calculate how many of the sites where the feature was active at the after_date
# did not have the feature active at the before_date
from google.cloud import bigquery
import pandas as pd


# Get sites from a list with the feature not active on a specific date
def get_active_sites_also_active_at_before_date_features(generator_tag1, generator_tag2, before_date, existing_sites):
  client = bigquery.Client(project=project_id)

  # Extract the origins from the existing_sites dataframe as a comma separated list
  existing_sites_list = ', '.join(f"'{origin}'" for origin in existing_sites['origin'])


  # 1. Identify Active and Non-Active Sites
  active_sites_query = f"""
    CREATE TEMP FUNCTION getFeature(payload STRING, generator_tag STRING)
    RETURNS STRING
    LANGUAGE js
    AS '''
      try {{
        var $ = JSON.parse(payload);
        var almanac = JSON.parse($._almanac);
        var generators = almanac['meta-nodes'].nodes.find(node => node.name == 'generator' && node.content.startsWith(generator_tag));
        if ( generators.length == 0 ) {{
          return "";
        }}
        var content =  generators.content;
        return content;
      }} catch (e) {{
        return "";
      }}
    ''';


    SELECT
      page AS origin
    FROM
      `httparchive.all.pages`,
       UNNEST(technologies) AS technologies

    WHERE
      technologies.technology = 'WordPress'
      AND date = PARSE_DATE('%Y-%m-%d', '{before_date}' )
      AND is_root_page = TRUE
      AND client = 'mobile'
      AND page IN ({existing_sites_list})
      AND getFeature(payload, '{generator_tag1}') != ""
      AND getFeature(payload, '{generator_tag2}') != ""
    LIMIT {limit}
  """

  active_sites_df = client.query(active_sites_query).to_dataframe()
  return active_sites_df

In [ ]:
#@markdown ## Get CWV changes for a set of sites between before and after dates
#@markdown
#@markdown Note: sites_df is a dataframe with an origin column containing the URLs.
#@markdown
#@markdown Returns:
#@markdown  * pct_eligible_origins_with_good_cwv_change
#@markdown  * pct_eligible_origins_with_good_lcp_change
#@markdown  * pct_eligible_origins_with_good_cls_change
#@markdown  * pct_eligible_origins_with_good_inp_change
#@markdown



import pdb
# Get the CWV change before/after for sites
def get_cwv_change_before_after(sites_df, before_date, after_date):
  client = bigquery.Client(project=project_id)
  # 0. Ensure the 'temp_dataset' dataset exists, or create it
  dataset_id = f"{project_id}.temp_dataset"
  try:
      client.get_dataset(dataset_id)  # Check if dataset exists
  except NotFound:
      dataset = bigquery.Dataset(dataset_id)
      dataset.location = "US"  # Set the location (adjust if needed)
      client.create_dataset(dataset)

  # 1. Create a temporary table with the list of origins
  schema = [bigquery.SchemaField("origin", "STRING")]
  job_config = bigquery.LoadJobConfig(schema=schema)
  job = client.load_table_from_dataframe(sites_df, f"{project_id}.temp_dataset.origins", job_config=job_config)
  job.result()  # Wait for the job to complete

  client = bigquery.Client(project=project_id)
  # 2. Collect CWV Data and Calculate Baselines
  cwv_query = f"""
  CREATE TEMP FUNCTION IS_GOOD(good FLOAT64, needs_improvement FLOAT64, poor FLOAT64)
    RETURNS BOOL
    AS (
      good / (good + needs_improvement + poor) >= 0.75
    );

  CREATE TEMP FUNCTION IS_NON_ZERO(good FLOAT64, needs_improvement FLOAT64, poor FLOAT64)
    RETURNS BOOL
    AS (
      good + needs_improvement + poor > 0
    );


  SELECT
      date,
      COUNT(DISTINCT origin) AS origins,
      SAFE_DIVIDE(COUNTIF(good_cwv), COUNTIF(any_lcp AND any_cls)) AS pct_eligible_origins_with_good_cwv,
      SAFE_DIVIDE(COUNTIF(good_lcp), COUNTIF(any_lcp)) AS pct_eligible_origins_with_good_lcp,
      SAFE_DIVIDE(COUNTIF(good_cls), COUNTIF(any_cls)) AS pct_eligible_origins_with_good_cls,
      SAFE_DIVIDE(COUNTIF(good_inp), COUNTIF(any_inp)) AS pct_eligible_origins_with_good_inp
    FROM
      (
        SELECT
          date AS date,
          origin,
          # Device phone or tablet as mobile, otherwise desktop.
          IF(device = 'phone' OR device = 'tablet', 'mobile', device) AS device,
          IS_NON_ZERO(fast_inp, avg_inp, slow_inp) AS any_inp,
          IS_GOOD(fast_inp, avg_inp, slow_inp) AS good_inp,
          IS_NON_ZERO(small_cls, medium_cls, large_cls) AS any_cls,
          IS_GOOD(small_cls, medium_cls, large_cls) AS good_cls,
          IS_NON_ZERO(fast_lcp, avg_lcp, slow_lcp) AS any_lcp,
          IS_GOOD(fast_lcp, avg_lcp, slow_lcp) AS good_lcp,
          (IS_GOOD(fast_inp, avg_inp, slow_inp) OR fast_inp IS NULL) AND IS_GOOD(small_cls, medium_cls, large_cls) AND IS_GOOD(fast_lcp, avg_lcp, slow_lcp) AS good_cwv
        FROM
          `chrome-ux-report.materialized.device_summary` AS cwvs
        WHERE
          (
            date = PARSE_DATE('%Y-%m-%d', '{before_date}') OR
            date = PARSE_DATE('%Y-%m-%d', '{after_date}' )
          )
          AND cwvs.device IN ('desktop', 'tablet', 'phone')
          # Restrict to sites that are in both dates
          AND CONCAT(cwvs.origin, '/') IN (SELECT origin FROM `{project_id}.temp_dataset.origins`)
        )
    GROUP BY
      date
    ORDER BY
      date
  """

  cwv_data = client.query(cwv_query).to_dataframe()

  # select the data from the after_date (by date column)
  cwv_after = cwv_data[cwv_data['date'] == pd.to_datetime(after_date)]
  cwv_before = cwv_data[cwv_data['date'] == pd.to_datetime(before_date)]

  # subtract the 'pct_eligible_origins_with_good_cwv' value at cwv_before from cwv_after
  pct_eligible_origins_with_good_cwv_change = cwv_after['pct_eligible_origins_with_good_cwv'].values[0] - cwv_before['pct_eligible_origins_with_good_cwv'].values[0]
  pct_eligible_origins_with_good_lcp_change = cwv_after['pct_eligible_origins_with_good_lcp'].values[0] - cwv_before['pct_eligible_origins_with_good_lcp'].values[0]
  pct_eligible_origins_with_good_cls_change = cwv_after['pct_eligible_origins_with_good_cls'].values[0] - cwv_before['pct_eligible_origins_with_good_cls'].values[0]
  pct_eligible_origins_with_good_inp_change = cwv_after['pct_eligible_origins_with_good_inp'].values[0] - cwv_before['pct_eligible_origins_with_good_inp'].values[0]

  # 3. Clean up: Delete the temporary table (optional but good practice)
  client.delete_table(f"{project_id}.temp_dataset.origins")

  return [
      pct_eligible_origins_with_good_cwv_change,
      pct_eligible_origins_with_good_lcp_change,
      pct_eligible_origins_with_good_cls_change,
      pct_eligible_origins_with_good_inp_change
  ]

### Breakout by device

In [ ]:
#@markdown ## Get CWV changes for a set of sites between before and after dates
#@markdown ### Broken out by device
#@markdown `get_cwv_change_before_after_by_device`
#@markdown
#@markdown Note: sites_df is a dataframe with an origin column containing the URLs.
#@markdown
#@markdown Returns:
#@markdown  * pct_eligible_origins_with_good_cwv_change_mobile
#@markdown  * pct_eligible_origins_with_good_cwv_change_mobile,
#@markdown  * pct_eligible_origins_with_good_lcp_change_mobile,
#@markdown  * pct_eligible_origins_with_good_cls_change_mobile,
#@markdown  * pct_eligible_origins_with_good_inp_change_mobile,
#@markdown  * pct_eligible_origins_with_good_cwv_change_desktop,
#@markdown  * pct_eligible_origins_with_good_lcp_change_desktop,
#@markdown  * pct_eligible_origins_with_good_cls_change_desktop,
#@markdown  * pct_eligible_origins_with_good_inp_change_desktop



In [ ]:

import pdb
# Get the CWV change before/after for sites
def get_cwv_change_before_after_by_device(sites_df, before_date, after_date):
  client = bigquery.Client(project=project_id)
  # 0. Ensure the 'temp_dataset' dataset exists, or create it
  dataset_id = f"{project_id}.temp_dataset"
  try:
      client.get_dataset(dataset_id)  # Check if dataset exists
  except NotFound:
      dataset = bigquery.Dataset(dataset_id)
      dataset.location = "US"  # Set the location (adjust if needed)
      client.create_dataset(dataset)

  # 1. Create a temporary table with the list of origins
  schema = [bigquery.SchemaField("origin", "STRING")]
  job_config = bigquery.LoadJobConfig(schema=schema)
  job = client.load_table_from_dataframe(sites_df, f"{project_id}.temp_dataset.origins", job_config=job_config)
  job.result()  # Wait for the job to complete

  client = bigquery.Client(project=project_id)
  # 2. Collect CWV Data and Calculate Baselines
  cwv_query = f"""
  CREATE TEMP FUNCTION IS_GOOD(good FLOAT64, needs_improvement FLOAT64, poor FLOAT64)
    RETURNS BOOL
    AS (
      good / (good + needs_improvement + poor) >= 0.75
    );

  CREATE TEMP FUNCTION IS_NON_ZERO(good FLOAT64, needs_improvement FLOAT64, poor FLOAT64)
    RETURNS BOOL
    AS (
      good + needs_improvement + poor > 0
    );


  SELECT
      date,
      device,
      COUNT(DISTINCT origin) AS origins,
      SAFE_DIVIDE(COUNTIF(good_cwv), COUNTIF(any_lcp AND any_cls)) AS pct_eligible_origins_with_good_cwv,
      SAFE_DIVIDE(COUNTIF(good_lcp), COUNTIF(any_lcp)) AS pct_eligible_origins_with_good_lcp,
      SAFE_DIVIDE(COUNTIF(good_cls), COUNTIF(any_cls)) AS pct_eligible_origins_with_good_cls,
      SAFE_DIVIDE(COUNTIF(good_inp), COUNTIF(any_inp)) AS pct_eligible_origins_with_good_inp
    FROM
      (
        SELECT
          date AS date,
          origin,
          # Device phone or tablet as mobile, otherwise desktop.
          IF(device = 'phone' OR device = 'tablet', 'mobile', device) AS device,
          IS_NON_ZERO(fast_inp, avg_inp, slow_inp) AS any_inp,
          IS_GOOD(fast_inp, avg_inp, slow_inp) AS good_inp,
          IS_NON_ZERO(small_cls, medium_cls, large_cls) AS any_cls,
          IS_GOOD(small_cls, medium_cls, large_cls) AS good_cls,
          IS_NON_ZERO(fast_lcp, avg_lcp, slow_lcp) AS any_lcp,
          IS_GOOD(fast_lcp, avg_lcp, slow_lcp) AS good_lcp,
          (IS_GOOD(fast_inp, avg_inp, slow_inp) OR fast_inp IS NULL) AND IS_GOOD(small_cls, medium_cls, large_cls) AND IS_GOOD(fast_lcp, avg_lcp, slow_lcp) AS good_cwv
        FROM
          `chrome-ux-report.materialized.device_summary` AS cwvs
        WHERE
          (
            date = PARSE_DATE('%Y-%m-%d', '{before_date}') OR
            date = PARSE_DATE('%Y-%m-%d', '{after_date}' )
          )
          AND cwvs.device IN ('desktop', 'tablet', 'phone')
          # Restrict to sites that are in both dates
          AND CONCAT(cwvs.origin, '/') IN (SELECT origin FROM `{project_id}.temp_dataset.origins`)
        )
    GROUP BY
      date, device
    ORDER BY
      date
  """

  cwv_data = client.query(cwv_query).to_dataframe()

  # select the data from the after_date (by date and device columns)
  # mobile data
  cwv_after_mobile = cwv_data[(cwv_data['date'] == pd.to_datetime(after_date)) & (cwv_data['device'] == 'mobile')]
  cwv_before_mobile = cwv_data[(cwv_data['date'] == pd.to_datetime(before_date)) & (cwv_data['device'] == 'mobile')]

  # desktop data
  cwv_after_desktop = cwv_data[(cwv_data['date'] == pd.to_datetime(after_date)) & (cwv_data['device'] == 'desktop')]
  cwv_before_desktop = cwv_data[(cwv_data['date'] == pd.to_datetime(before_date)) & (cwv_data['device'] == 'desktop')]


  # subtract the 'pct_eligible_origins_with_good_cwv' value at cwv_before from cwv_after
  pct_eligible_origins_with_good_cwv_change_mobile = cwv_after_mobile['pct_eligible_origins_with_good_cwv'].values[0] - cwv_before_mobile['pct_eligible_origins_with_good_cwv'].values[0]
  pct_eligible_origins_with_good_lcp_change_mobile = cwv_after_mobile['pct_eligible_origins_with_good_lcp'].values[0] - cwv_before_mobile['pct_eligible_origins_with_good_lcp'].values[0]
  pct_eligible_origins_with_good_cls_change_mobile = cwv_after_mobile['pct_eligible_origins_with_good_cls'].values[0] - cwv_before_mobile['pct_eligible_origins_with_good_cls'].values[0]
  pct_eligible_origins_with_good_inp_change_mobile = cwv_after_mobile['pct_eligible_origins_with_good_inp'].values[0] - cwv_before_mobile['pct_eligible_origins_with_good_inp'].values[0]

  pct_eligible_origins_with_good_cwv_change_desktop = cwv_after_desktop['pct_eligible_origins_with_good_cwv'].values[0] - cwv_before_desktop['pct_eligible_origins_with_good_cwv'].values[0]
  pct_eligible_origins_with_good_lcp_change_desktop = cwv_after_desktop['pct_eligible_origins_with_good_lcp'].values[0] - cwv_before_desktop['pct_eligible_origins_with_good_lcp'].values[0]
  pct_eligible_origins_with_good_cls_change_desktop = cwv_after_desktop['pct_eligible_origins_with_good_cls'].values[0] - cwv_before_desktop['pct_eligible_origins_with_good_cls'].values[0]
  pct_eligible_origins_with_good_inp_change_desktop = cwv_after_desktop['pct_eligible_origins_with_good_inp'].values[0] - cwv_before_desktop['pct_eligible_origins_with_good_inp'].values[0]

  # 3. Clean up: Delete the temporary table (optional but good practice)
  client.delete_table(f"{project_id}.temp_dataset.origins")

  return [
      pct_eligible_origins_with_good_cwv_change_mobile,
      pct_eligible_origins_with_good_lcp_change_mobile,
      pct_eligible_origins_with_good_cls_change_mobile,
      pct_eligible_origins_with_good_inp_change_mobile,
      pct_eligible_origins_with_good_cwv_change_desktop,
      pct_eligible_origins_with_good_lcp_change_desktop,
      pct_eligible_origins_with_good_cls_change_desktop,
      pct_eligible_origins_with_good_inp_change_desktop,
      cwv_before_mobile,
      cwv_after_mobile,
      cwv_before_desktop,
      cwv_after_desktop
  ]

In [ ]:
#@markdown ## Calculate impact minus baseline

# calculate the impact by subracting the baseline from the change
def calculate_feature_impact(change, baseline):
  cwv_change = change[0] - baseline[0]
  lcp_change = change[1] - baseline[1]
  cls_change = change[2] - baseline[2]
  inp_change = change[3] - baseline[3]
  return {
    'pct_good_cwv_change': "{:.2%}".format(cwv_change),
    'pct_good_lcp_change': "{:.2%}".format(lcp_change),
    'pct_good_cls_change': "{:.2%}".format(cls_change),
    'pct_good_inp_change': "{:.2%}".format(inp_change)
  }

In [ ]:
#@markdown ## Calculate impact minus baseline by device

# calculate the impact by subracting the baseline from the change
def calculate_feature_impact_by_device(change, baseline):
  cwv_change_mobile = change[0] - baseline[0]
  lcp_change_mobile = change[1] - baseline[1]
  cls_change_mobile = change[2] - baseline[2]
  inp_change_mobile = change[3] - baseline[3]
  cwv_change_desktop = change[4] - baseline[4]
  lcp_change_desktop = change[5] - baseline[5]
  cls_change_desktop = change[6] - baseline[6]
  inp_change_desktop = change[7] - baseline[7]
  return {
    'pct_good_cwv_change_mobile': "{:.2%}".format(cwv_change_mobile),
    'pct_good_lcp_change_mobile': "{:.2%}".format(lcp_change_mobile),
    'pct_good_cls_change_mobile': "{:.2%}".format(cls_change_mobile),
    'pct_good_inp_change_mobile': "{:.2%}".format(inp_change_mobile),
    'pct_good_cwv_change_desktop': "{:.2%}".format(cwv_change_desktop),
    'pct_good_lcp_change_desktop': "{:.2%}".format(lcp_change_desktop),
    'pct_good_cls_change_desktop': "{:.2%}".format(cls_change_desktop),
    'pct_good_inp_change_desktop': "{:.2%}".format(inp_change_desktop)
  }

In [ ]:
#@markdown ## Measure feature performance impact minus baseline
#@markdown
#@markdown ### Note:
#@markdown * This helper combines device data.
def query_cwv_compare_feature_to_baseline(generator_tag, before_date, after_date):
  active_sites = get_sites_with_feature_active(generator_tag, after_date)
  count_active_sites = active_sites.count()
  inactive_sites = get_sites_with_feature_inactive(generator_tag, after_date)
  count_inactive_sites = inactive_sites.count()

  # Count feature active sites that were also feature active at the before date.
  active_at_from_date = get_active_sites_also_active_at_before_date(generator_tag, before_date, active_sites)
  count_active_at_from_date = active_at_from_date.count()

  # Calculate the percentage of count_active_at_from_date (which might be 0 so use safe divide)
  if count_active_sites['origin'] > 0:
    also_active_at_before = (count_active_at_from_date['origin'] / count_active_sites['origin']) * 100
  else:
    also_active_at_before = 0

  # Calculate CWV change
  cwv_changes_active_sites = get_cwv_change_before_after(active_sites, before_date, after_date )
  cwv_changes_inactive_sites = get_cwv_change_before_after(inactive_sites, before_date, after_date )

  final_results = calculate_feature_impact(cwv_changes_active_sites, cwv_changes_inactive_sites)
  final_results['feature_active_sites'] = count_active_sites['origin']
  final_results['feature_inactive_sites'] = count_inactive_sites['origin']
  final_results['also_active_at_before'] = "{:.2%}".format(also_active_at_before)

  return final_results

In [ ]:
#@markdown ## Measure feature performance impact minus baseline
#@markdown ### Breakout by device
def query_cwv_compare_feature_to_baseline_by_device(generator_tag, before_date, after_date):
  active_sites = get_sites_with_feature_active(generator_tag, after_date)
  count_active_sites = active_sites.count()
  inactive_sites = get_sites_with_feature_inactive(generator_tag, after_date)
  count_inactive_sites = inactive_sites.count()

  # Count feature active sites that were also feature active at the before date.
  active_at_from_date = get_active_sites_also_active_at_before_date(generator_tag, before_date, active_sites)
  count_active_at_from_date = active_at_from_date.count()

  # Calculate the percentage of count_active_at_from_date (which might be 0 so use safe divide)
  if count_active_sites['origin'] > 0:
    also_active_at_before = (count_active_at_from_date['origin'] / count_active_sites['origin']) * 100
  else:
    also_active_at_before = 0

  # Calculate CWV change
  cwv_changes_active_sites = get_cwv_change_before_after_by_device(active_sites, before_date, after_date )
  cwv_changes_inactive_sites = get_cwv_change_before_after_by_device(inactive_sites, before_date, after_date )

  final_results = calculate_feature_impact_by_device(cwv_changes_active_sites, cwv_changes_inactive_sites)
  final_results['feature_active_sites'] = count_active_sites['origin']
  final_results['feature_inactive_sites'] = count_inactive_sites['origin']
  final_results['also_active_at_before'] = "{:.2%}".format(also_active_at_before)
  final_results['before_date'] =  before_date
  final_results['after_date'] =  after_date
  final_results['generator_tag'] =  generator_tag
  final_results['cwv_changes_active_sites'] =  cwv_changes_active_sites
  final_results['cwv_changes_inactive_sites'] =  cwv_changes_inactive_sites

  return final_results

In [ ]:
#@markdown ## Measure feature performance impact minus baseline
#@markdown ### Breakout by device
def query_cwv_compare_feature_to_baseline_by_device_multiple_tags(generator_tag1, generator_tag2, before_date, after_date):

  active_sites = get_sites_with_features_active(generator_tag1, generator_tag2, after_date)
  count_active_sites = active_sites.count()
  inactive_sites = get_sites_with_features_inactive(generator_tag1, generator_tag2, after_date)
  count_inactive_sites = inactive_sites.count()

  # Count feature active sites that were also feature active at the before date.
  active_at_from_date = get_active_sites_also_active_at_before_date_features(generator_tag1, generator_tag2, before_date, active_sites)
  count_active_at_from_date = active_at_from_date.count()

  # Calculate the percentage of count_active_at_from_date (which might be 0 so use safe divide)
  if count_active_sites['origin'] > 0:
    also_active_at_before = (count_active_at_from_date['origin'] / count_active_sites['origin']) * 100
  else:
    also_active_at_before = 0

  # Calculate CWV change
  cwv_changes_active_sites = get_cwv_change_before_after_by_device(active_sites, before_date, after_date )
  cwv_changes_inactive_sites = get_cwv_change_before_after_by_device(inactive_sites, before_date, after_date )

  final_results = calculate_feature_impact_by_device(cwv_changes_active_sites, cwv_changes_inactive_sites)
  final_results['feature_active_sites'] = count_active_sites['origin']
  final_results['feature_inactive_sites'] = count_inactive_sites['origin']
  final_results['also_active_at_before'] = "{:.2%}".format(also_active_at_before)
  final_results['before_date'] =  before_date
  final_results['after_date'] =  after_date
  final_results['generator_tag1'] =  generator_tag1
  final_results['generator_tag2'] =  generator_tag2
  final_results['cwv_changes_active_sites'] =  cwv_changes_active_sites
  final_results['cwv_changes_inactive_sites'] =  cwv_changes_inactive_sites

  return final_results

# Helper use examples

In [ ]:
elementor_data = query_cwv_for_technology_over_dates('Elementor')
elementor_data.to_dataframe()

KeyboardInterrupt: 

In [ ]:
active_sites = get_sites_with_feature_active('speculation-rules', '2024-11-01')
active_sites.head(5)

# count active sites
count_active_sites = active_sites.count()
print(count_active_sites)

In [ ]:
get_sites_with_features_active('embed-optimizer', 'optimization-detective', '2024-09-01')

In [ ]:
inactive_sites = get_sites_with_feature_inactive('speculation-rules', '2024-08-01')
inactive_sites.head(5)

# count inactive sites
count_inactive_sites = inactive_sites.count()
print(count_inactive_sites)

origin    50000
dtype: int64


In [ ]:
sites = get_sites_with_features_inactive( 'embed-optimizer', 'optimization-detective', '2024-09-01')
sites.head(500)

origin
0                   https://mrd.cash/
1           https://www.handipet.org/
2    https://www.mimasaka-no-kuni.jp/
3           https://soundcity.com.ar/
4         https://ciclismoarg.com.ar/
..                                ...
495                 https://ivadi.es/
496  https://meuesquematizado.com.br/
497     https://safemedicinedrop.com/
498      https://visittrollaskagi.is/
499     https://www.plazahyundai.com/

[500 rows x 1 columns]

In [ ]:
previously_not_active = get_active_sites_also_active_at_before_date('speculation-rules', '2024-05-01', active_sites)
previously_not_active.head(5)

# count active sites
count_previously_not_active = previously_not_active.count()
print(count_previously_not_active)

origin    2960
dtype: int64


In [ ]:
cwv_changes_active_sites = get_cwv_change_before_after(active_sites, '2024-03-01', '2024-08-01' )
print(cwv_changes_active_sites)

[0.06232002113378332, 0.06346816102047553, 0.03573906737828336, 0.044142435735356034]


In [ ]:
cwv_changes_active_sites_by_device = get_cwv_change_before_after_by_device(active_sites, '2024-03-01', '2024-08-01' )
print(cwv_changes_active_sites_by_device)

[0.07083488781153219, 0.06909267366979688, 0.03922572086938758, 0.08127807033918977, 0.053894219906421015, 0.05999325206027517, 0.026095263217394526, 0.0027941094172748704]


In [ ]:
cwv_changes_inactive_sites = get_cwv_change_before_after(inactive_sites, '2024-03-01', '2024-08-01' )
print(cwv_changes_inactive_sites)

[0.03842766935669645, 0.03281879625688, 0.016236264348328477, 0.036834856975053176]


In [ ]:
cwv_changes_inactive_sites_by_device = get_cwv_change_before_after_by_device(inactive_sites, '2024-03-01', '2024-08-01' )
print(cwv_changes_inactive_sites_by_device)

[0.04525254428354497, 0.03586424508053565, 0.012105841662442773, 0.06688614771352841, 0.030943523718571342, 0.03481560556441132, 0.01572887912168608, 0.0004040350745310173]


In [ ]:
final_results = calculate_feature_impact(cwv_changes_active_sites, cwv_changes_inactive_sites)
print(final_results)


{'pct_good_cwv_change': '2.39%', 'pct_good_lcp_change': '3.06%', 'pct_good_cls_change': '1.95%', 'pct_good_inp_change': '0.73%'}


In [ ]:
final_results = calculate_feature_impact_by_device(cwv_changes_active_sites_by_device, cwv_changes_inactive_sites_by_device)
print(final_results)


{'pct_good_cwv_change_mobile': '2.56%', 'pct_good_lcp_change_mobile': '3.32%', 'pct_good_cls_change_mobile': '2.71%', 'pct_good_inp_change_mobile': '1.44%', 'pct_good_cwv_change_desktop': '2.30%', 'pct_good_lcp_change_desktop': '2.52%', 'pct_good_cls_change_desktop': '1.04%', 'pct_good_inp_change_desktop': '0.24%'}


In [ ]:
results = query_cwv_compare_feature_to_baseline( 'speculation-rules', '2024-03-01', '2024-08-01' )
print(results)

{'pct_good_cwv_change': '2.42%', 'pct_good_lcp_change': '3.06%', 'pct_good_cls_change': '1.98%', 'pct_good_inp_change': '0.82%', 'feature_active_sites': 7203, 'feature_inactive_sites': 50000, 'also_active_at_before': '0.00%'}


In [ ]:
results = query_cwv_compare_feature_to_baseline_by_device( 'speculation-rules', '2024-03-01', '2024-08-01' )
print(results)

{'pct_good_cwv_change_mobile': '2.60%', 'pct_good_lcp_change_mobile': '3.39%', 'pct_good_cls_change_mobile': '2.75%', 'pct_good_inp_change_mobile': '1.52%', 'pct_good_cwv_change_desktop': '2.39%', 'pct_good_lcp_change_desktop': '2.55%', 'pct_good_cls_change_desktop': '1.09%', 'pct_good_inp_change_desktop': '0.23%', 'feature_active_sites': 7203, 'feature_inactive_sites': 50000, 'also_active_at_before': '0.00%', 'before_date': '2024-03-01', 'after_date': '2024-08-01', 'generator_tag': 'speculation-rules', 'cwv_changes_active_sites': [0.07083488781153219, 0.06909267366979688, 0.03922572086938758, 0.08127807033918977, 0.053894219906421015, 0.05999325206027517, 0.026095263217394526, 0.0027941094172748704], 'cwv_changes_inactive_sites': [0.04482710642311871, 0.03515486832303927, 0.011717077581957724, 0.06609143742833012, 0.02997313470714902, 0.034507587443841525, 0.015172879563230546, 0.0005163767055975654]}


In [ ]:
# show results as a table
import pandas as pd
df = pd.DataFrame([results])
df

pct_good_cwv_change_mobile pct_good_lcp_change_mobile  \
0                      2.60%                      3.39%   

  pct_good_cls_change_mobile pct_good_inp_change_mobile  \
0                      2.75%                      1.52%   

  pct_good_cwv_change_desktop pct_good_lcp_change_desktop  \
0                       2.39%                       2.55%   

  pct_good_cls_change_desktop pct_good_inp_change_desktop  \
0                       1.09%                       0.23%   

   feature_active_sites  feature_inactive_sites also_active_at_before  \
0                  7203                   50000                 0.00%   

  before_date  after_date      generator_tag  \
0  2024-03-01  2024-08-01  speculation-rules   

                            cwv_changes_active_sites  \
0  [0.07083488781153219, 0.06909267366979688, 0.0...   

                          cwv_changes_inactive_sites  
0  [0.04482710642311871, 0.03515486832303927, 0.0...

# Performance by Feature Queries

## Notes
* `inactive_to_active_percent` Shows the percent of feature-active sites at the after date that __were also feature-active__ at the before date. Ideally this should be 0, meaning none of the sites had the feature ative at the before date.


## Speculative Loading

In [ ]:
latest_dataset = '2024-09-01'

In [ ]:
#@markdown ### Compare before/after
#@markdown * `before_date`: a date to analyze where the feature is not enabled
#@markdown * `after_date`: a date to analyze where the feature is enabled
#@markdown * `generator`: the generator tag indicating a feature is installed
#@markdown * `inactive_to_active_percent` Shows the percent of feature-active sites at the after date that were also feature-active at the before date.

before_date = '2024-03-01'
after_date = latest_dataset
generator_tag = 'speculation-rules'

results_sl = query_cwv_compare_feature_to_baseline_by_device(generator_tag, before_date, after_date)
print(results_sl)

{'pct_good_cwv_change_mobile': '2.04%', 'pct_good_lcp_change_mobile': '2.00%', 'pct_good_cls_change_mobile': '2.00%', 'pct_good_inp_change_mobile': '1.33%', 'pct_good_cwv_change_desktop': '2.25%', 'pct_good_lcp_change_desktop': '2.55%', 'pct_good_cls_change_desktop': '1.59%', 'pct_good_inp_change_desktop': '-0.24%', 'feature_active_sites': 9091, 'feature_inactive_sites': 50000, 'also_active_at_before': '0.00%', 'before_date': '2024-03-01', 'after_date': '2024-09-01', 'generator_tag': 'speculation-rules', 'cwv_changes_active_sites': [0.0709573638372546, 0.05973671280401477, 0.03339427392262129, 0.09929041920330417, 0.05443899666326818, 0.06367646788742376, 0.02837772363253499, -0.0026272786983606577], 'cwv_changes_inactive_sites': [0.050594884631586345, 0.03974626020874489, 0.013417786565544043, 0.08595551937012391, 0.031957622667799446, 0.03816732623091601, 0.012432157707554903, -0.00018933025299994188]}


## Image Prioitizer

In [ ]:
# image-prioritizer
before_date = '2024-03-01'
after_date = latest_dataset
generator_tag = 'image-prioritizer'

results_ip = query_cwv_compare_feature_to_baseline_by_device(generator_tag, before_date, after_date)
print(results_ip)

{'pct_good_cwv_change_mobile': '1.83%', 'pct_good_lcp_change_mobile': '2.63%', 'pct_good_cls_change_mobile': '2.02%', 'pct_good_inp_change_mobile': '1.07%', 'pct_good_cwv_change_desktop': '3.63%', 'pct_good_lcp_change_desktop': '3.64%', 'pct_good_cls_change_desktop': '2.66%', 'pct_good_inp_change_desktop': '-0.46%', 'feature_active_sites': 3057, 'feature_inactive_sites': 50000, 'also_active_at_before': '0.00%', 'before_date': '2024-04-01', 'after_date': '2024-09-01', 'generator_tag': 'image-prioritizer', 'cwv_changes_active_sites': [0.06355639390247644, 0.066255044344453, 0.025530920421860004, 0.08869432502523766, 0.06324726213202053, 0.06865713642895399, 0.034364047044162294, -0.004424134395824675], 'cwv_changes_inactive_sites': [0.04529243087001833, 0.039932468951196454, 0.005380117484358293, 0.07796061197519022, 0.02694167020240129, 0.03227752930248928, 0.007753865162267282, 0.00015203821501585946]}


## Embed Optimizer




In [ ]:
# embed-optimizer
before_date = '2024-07-01'
after_date = latest_dataset
generator_tag = 'embed-optimizer'

results_eo = query_cwv_compare_feature_to_baseline_by_device(generator_tag, before_date, after_date)
print(results_eo)

{'pct_good_cwv_change_mobile': '-5.69%', 'pct_good_lcp_change_mobile': '-4.23%', 'pct_good_cls_change_mobile': '-0.57%', 'pct_good_inp_change_mobile': '0.11%', 'pct_good_cwv_change_desktop': '-0.83%', 'pct_good_lcp_change_desktop': '-4.91%', 'pct_good_cls_change_desktop': '0.91%', 'pct_good_inp_change_desktop': '-0.37%', 'feature_active_sites': 4908, 'feature_inactive_sites': 50000, 'also_active_at_before': '5906.68%', 'before_date': '2024-07-01', 'after_date': '2024-09-01', 'generator_tag': 'embed-optimizer', 'cwv_changes_active_sites': [-0.041306793074358306, -0.031142749330665964, -0.009310373802833838, 0.03288217754941303, -0.00780285351372112, -0.04850123311220522, 0.010024549239471159, -0.005046772644276998], 'cwv_changes_inactive_sites': [0.01555233539948292, 0.011153826487459773, -0.0036123086688277795, 0.03178291363875008, 0.0005148192916936134, 0.0005865276079072279, 0.0008919736799152256, -0.0013168643303140826]}


## Modern Image Formats

In [ ]:
# webp-uploads
before_date = '2024-03-01'
after_date = latest_dataset
generator_tag = 'webp-uploads'

results_mi = query_cwv_compare_feature_to_baseline_by_device(generator_tag, before_date, after_date)
print(results_mi)

{'pct_good_cwv_change_mobile': '1.86%', 'pct_good_lcp_change_mobile': '1.26%', 'pct_good_cls_change_mobile': '2.31%', 'pct_good_inp_change_mobile': '1.57%', 'pct_good_cwv_change_desktop': '2.31%', 'pct_good_lcp_change_desktop': '2.14%', 'pct_good_cls_change_desktop': '1.45%', 'pct_good_inp_change_desktop': '0.15%', 'feature_active_sites': 16148, 'feature_inactive_sites': 50000, 'also_active_at_before': '0.00%', 'before_date': '2024-01-01', 'after_date': '2024-09-01', 'generator_tag': 'webp-uploads', 'cwv_changes_active_sites': [0.09053611980768622, 0.06681956845397613, 0.04422785761234971, 0.13775801636582619, 0.053067897464070646, 0.055216839004633256, 0.029493570947297654, 0.003979401208744959], 'cwv_changes_inactive_sites': [0.0719599926198663, 0.05425106123086576, 0.021089317940479635, 0.1220972067245063, 0.030003443405208163, 0.033798004781138036, 0.015025429495077125, 0.002452523250483174]}


## Enhanced Image Sizes

In [ ]:
# auto-sizes
before_date = '2024-03-01'
after_date = latest_dataset
generator_tag = 'auto-sizes'

results_is = query_cwv_compare_feature_to_baseline_by_device(generator_tag, before_date, after_date)
print(results_is)

{'pct_good_cwv_change_mobile': '0.77%', 'pct_good_lcp_change_mobile': '-0.22%', 'pct_good_cls_change_mobile': '2.33%', 'pct_good_inp_change_mobile': '2.50%', 'pct_good_cwv_change_desktop': '3.02%', 'pct_good_lcp_change_desktop': '1.37%', 'pct_good_cls_change_desktop': '3.14%', 'pct_good_inp_change_desktop': '0.18%', 'feature_active_sites': 5633, 'feature_inactive_sites': 50000, 'also_active_at_before': '0.00%', 'before_date': '2024-03-01', 'after_date': '2024-09-01', 'generator_tag': 'auto-sizes', 'cwv_changes_active_sites': [0.06442163880919188, 0.048145394148988996, 0.0325715565983854, 0.11997871774408086, 0.06243687002187076, 0.05522724145910157, 0.041617845644969065, 0.001961164045756192], 'cwv_changes_inactive_sites': [0.05675288022675129, 0.05037639877576028, 0.009301400069805288, 0.09498100979108803, 0.03222344332123689, 0.041554902302256336, 0.010225594823027317, 0.00014161616508323593]}


## Performant Translations

In [ ]:
# performant-translations
before_date = '2024-03-01'
after_date = latest_dataset
generator_tag = 'performant-translations'

results_is = query_cwv_compare_feature_to_baseline_by_device(generator_tag, before_date, after_date)
print(results_is)

## Web Worker Offloading

In [ ]:
# web-worker-offloading
before_date = '2024-07-01'
after_date = latest_dataset
generator_tag = 'web-worker-offloading'

results_is = query_cwv_compare_feature_to_baseline_by_device(generator_tag, before_date, after_date)
print(results_is)

{'pct_good_cwv_change_mobile': '0.94%', 'pct_good_lcp_change_mobile': '-1.22%', 'pct_good_cls_change_mobile': '5.04%', 'pct_good_inp_change_mobile': '1.29%', 'pct_good_cwv_change_desktop': '0.55%', 'pct_good_lcp_change_desktop': '-1.35%', 'pct_good_cls_change_desktop': '4.56%', 'pct_good_inp_change_desktop': '0.10%', 'feature_active_sites': 601, 'feature_inactive_sites': 50000, 'also_active_at_before': '0.00%', 'before_date': '2024-07-01', 'after_date': '2024-11-01', 'generator_tag': 'web-worker-offloading', 'cwv_changes_active_sites': [0.026853975535168162, 0.0001429762897652842, 0.046814342865609704, 0.04866273605058535, 0.005261578120310084, -0.007205877183732334, 0.039323973650941535, 0.000566951860632936,          date  device  origins  pct_eligible_origins_with_good_cwv  \
1  2024-07-01  mobile      312                            0.275229   

   pct_eligible_origins_with_good_lcp  pct_eligible_origins_with_good_cls  \
1                            0.412844                         

In [ ]:
latest_dataset = '2024-11-01'

## Embed Optimizer plus Optimization detective


In [ ]:
# this will use a slightly different approach because we are looking for sites with two features enabled.
before_date = '2024-07-01'
after_date = latest_dataset
generator_tag1 = 'optimization-detective'
generator_tag2 = 'embed-optimizer'

results_is = query_cwv_compare_feature_to_baseline_by_device_multiple_tags(generator_tag1, generator_tag2, before_date, after_date)
print(results_is)



{'pct_good_cwv_change_mobile': '0.20%', 'pct_good_lcp_change_mobile': '1.09%', 'pct_good_cls_change_mobile': '2.08%', 'pct_good_inp_change_mobile': '-0.48%', 'pct_good_cwv_change_desktop': '4.39%', 'pct_good_lcp_change_desktop': '2.12%', 'pct_good_cls_change_desktop': '3.70%', 'pct_good_inp_change_desktop': '-0.22%', 'feature_active_sites': 3523, 'feature_inactive_sites': 50000, 'also_active_at_before': '1481.69%', 'before_date': '2024-07-01', 'after_date': '2024-11-01', 'generator_tag1': 'optimization-detective', 'generator_tag2': 'embed-optimizer', 'cwv_changes_active_sites': [0.022084835266597713, 0.026946373942071167, 0.014579789123231879, 0.03380411086302515, 0.04506952879183501, 0.031181994226598397, 0.032788667906710534, -0.0035211267605633756,          date  device  origins  pct_eligible_origins_with_good_cwv  \
0  2024-07-01  mobile     1715                            0.260748   

   pct_eligible_origins_with_good_lcp  pct_eligible_origins_with_good_cls  \
0                   

# Graveyard

In [ ]:
from google.cloud import bigquery
import pandas as pd

def analyse_performance_impact_of_feature(generator_tag, after_date=None):

  client = bigquery.Client()

  # 1. Identify Active and Non-Active Sites
  active_sites_query = f"""
  CREATE TEMP FUNCTION getFeature(payload STRING)
  RETURNS STRING
  LANGUAGE js
  AS '''
    try {{
      var $ = JSON.parse(payload);
      var almanac = JSON.parse($._almanac);
      var generators = almanac['meta-nodes'].nodes.find(node => node.name == 'generator' && node.content.startsWith('$.{{generator}}'));
      if ( generators.length == 0 ) {{
        return "";
      }}
      var content =  generators.content;
      return content;
    }} catch (e) {{
      return "";
    }}
  ''';

  SELECT * FROM
  (
      SELECT
        page AS origin,
        client AS device,
        date,
        getFeature(payload) as feature
      FROM
        `httparchive.all.pages`,
        UNNEST(technologies) AS technologies
      WHERE
        technologies.technology = 'WordPress'
        AND  date = PARSE_DATE('%Y_%m_%d', '{after_date}' )
        AND is_root_page = TRUE
  )
  WHERE feature != ""
  LIMIT 10000
  """

  non_active_sites_query = f"""
  CREATE TEMP FUNCTION getFeature(payload STRING)
  RETURNS STRING
  LANGUAGE js
  AS '''
    try {{
      var $ = JSON.parse(payload);
      var almanac = JSON.parse($._almanac);
      var generators = almanac['meta-nodes'].nodes.find(node => node.name == 'generator' && node.content.startsWith('$.{{generator}}'));
      if ( generators.length == 0 ) {{
        return "";
      }}
      var content =  generators.content;
      return content;
    }} catch (e) {{
      return "";
    }}
  ''';

  SELECT * FROM
  (
      SELECT
        page AS origin,
        client AS device,
        date,
        getFeature(payload) as feature
      FROM
        `httparchive.all.pages`,
        UNNEST(technologies) AS technologies
      WHERE
        technologies.technology = 'WordPress'
        AND  date = PARSE_DATE('%Y_%m_%d', '{after_date}' )
        AND is_root_page = TRUE
  )
  WHERE feature = ""
  LIMIT 10000
  """

  active_sites_df = client.query(active_sites_query).to_dataframe()
  non_active_sites_df = client.query(non_active_sites_query).to_dataframe()


  # 2. Collect CWV Data and Calculate Baselines
  def calculate_cwv_stats(df, active=False):
    cwv_metrics = ['largest_contentful_paint', 'first_input_delay', 'cumulative_layout_shift']
    all_cwv_data = []

    for _, row in df.iterrows():
        for month_offset in range(14): # collect data for the past 14 months
            query_date = row['parse_date'] - pd.DateOffset(months=month_offset)
            query_string = f"""

            SELECT origin,
                IF(fast_lcp_count IS NOT NULL, fast_lcp_count / (fast_lcp_count + avg_lcp_count + slow_lcp_count), NULL) AS lcp_pass_rate,
                IF(fast_fid_count IS NOT NULL, fast_fid_count / (fast_fid_count + avg_fid_count + slow_fid_count), NULL) AS fid_pass_rate,
                IF(small_cls_count IS NOT NULL, small_cls_count / (small_cls_count + medium_cls_count + large_cls_count), NULL) AS cls_pass_rate,
                IF(good_inp_count IS NOT NULL, good_inp_count / (good_inp_count + ok_inp_count + poor_inp_count), NULL) AS inp_pass_rate
            FROM `chrome-ux-report.materialized.device_summary`
            WHERE origin = '{row["url"]}'
            AND DATE_TRUNC(date, MONTH) = DATE_TRUNC(DATE('{query_date}'), MONTH)
            """

            cwv_data = client.query(query_string).to_dataframe()
            if not cwv_data.empty:
                cwv_data['month'] = query_date # include the month for each metric
                cwv_data['active'] = active
                all_cwv_data.append(cwv_data)

    return pd.concat(all_cwv_data)

  # 3. Identify Feature Activation and Calculate Impact
  active_cwv_stats = calculate_cwv_stats(active_sites_df, active=True)
  non_active_cwv_stats = calculate_cwv_stats(non_active_sites_df)

  def calculate_feature_impact(active_cwv_stats):
    impact_data = []
    for url, group in active_cwv_stats.groupby('origin'):
        activation_month = group[group['active'] == True]['month'].min()
        if activation_month is not pd.NaT:
            before_activation = group[group['month'] == activation_month - pd.DateOffset(months=1)]
            after_activation = group[group['month'] == activation_month + pd.DateOffset(months=1)]

            if not before_activation.empty and not after_activation.empty:
                impact = after_activation.mean() - before_activation.mean()
                impact['url'] = url
                impact_data.append(impact)

    return pd.DataFrame(impact_data)

  feature_impact_df = calculate_feature_impact(active_cwv_stats)

  return feature_impact_df

In [ ]:
analyse_performance_impact_of_feature('speculation-rules', '2024_06_01')


## Example using Speculation Rules

In [ ]:
#@markdown ### Compare speculation rules before/after
results = query_cwv_compare_feature_to_baseline( 'speculation-rules', '2024-03-01', '2024-06-01' )
print(results)

### Helper to compare feature before / after

In [ ]:
# Restrict the query to on the from and to dates, and without and with a specific generator tag indicating a feature is active
def query_cwv_compare_dates_by_generator(technology, from_date, to_date, generator):
  """
    Queries Core Web Vitals metrics from HTTP Archive.

    Args:
        technology (str): The technology to filter by (e.g., 'WordPress').
        from_date (str): The start date in YYYY_MM_DD format.
        to_date (str): The end date in YYYY_MM_DD format.
        generator (str): The generator tag indicating a feature is installed.
    Returns:
        A BigQuery query result object containing CWV data.
  """
  # set to_date if not passed
  if not to_date:
    to_date = latest_dataset

  # set from date if not passed
  if not from_date:
    from_date = (datetime.strptime(to_date, '%Y_%m_%d').date() - timedelta(days=365)).strftime('%Y_%m_%d')


  query = f"""
  CREATE TEMP FUNCTION getFeature(payload STRING)
RETURNS STRING
LANGUAGE js
AS '''
  try {{
    var $ = JSON.parse(payload);
    var almanac = JSON.parse($._almanac);
    var generators = almanac['meta-nodes'].nodes.find(node => node.name == 'generator' && node.content.startsWith('$.{{generator}}'));
    if ( generators.length == 0 ) {{
      return "";
    }}
    var content =  generators.content;
    return content;
  }} catch (e) {{
    return "";
  }}
''';

CREATE TEMP FUNCTION IS_GOOD(good FLOAT64, needs_improvement FLOAT64, poor FLOAT64)
    RETURNS BOOL
    AS (
      good / (good + needs_improvement + poor) >= 0.75
    );

    CREATE TEMP FUNCTION IS_NON_ZERO(good FLOAT64, needs_improvement FLOAT64, poor FLOAT64)
    RETURNS BOOL
    AS (
      good + needs_improvement + poor > 0
    );
  WITH sites_available_on_from_or_to_date AS (
    SELECT
      page AS origin,
      client AS device,
      date,
      getFeature(payload) as feature
    FROM
      `httparchive.all.pages`,
      UNNEST(technologies) AS technologies
    WHERE
      technologies.technology = '{technology}'
      AND (
        ( date = PARSE_DATE('%Y_%m_%d', '{from_date}') ) OR
        ( date = PARSE_DATE('%Y_%m_%d', '{to_date}' ) )
      )
      AND is_root_page = TRUE

  ),
  site_on_to_date_with_feature AS (
   SELECT
    origin,
    device,
    date,
    feature
   FROM sites_available_on_from_or_to_date
   WHERE date = PARSE_DATE('%Y_%m_%d', '{to_date}' )
   AND feature != ""
    ),
  sites_on_from_date_without_feature AS (
    SELECT
      origin,
      device,
      date,
      feature
    FROM
      sites_available_on_from_or_to_date
    WHERE
      date = PARSE_DATE('%Y_%m_%d', '{from_date}')
      AND feature = ""
  ),
  sites_available_for_both_from_and_to AS (
    SELECT
      sites_available_on_from_or_to_date.origin
    FROM
      sites_available_on_from_or_to_date
    JOIN
      sites_on_from_date_without_feature
    ON (sites_available_on_from_or_to_date.origin = sites_on_from_date_without_feature.origin)
  ),
  cwv_metrics_for_origins AS (
    SELECT
      cwvs.date AS date,
      site_on_to_date_with_feature.origin AS origin,
      # Device phone or tablet as mobile, otherwise desktop.
      IF(cwvs.device = 'phone' OR cwvs.device = 'tablet', 'mobile', cwvs.device) AS device,
      IS_NON_ZERO(fast_inp, avg_inp, slow_inp) AS any_inp,
      IS_GOOD(fast_inp, avg_inp, slow_inp) AS good_inp,
      IS_NON_ZERO(small_cls, medium_cls, large_cls) AS any_cls,
      IS_GOOD(small_cls, medium_cls, large_cls) AS good_cls,
      IS_NON_ZERO(fast_lcp, avg_lcp, slow_lcp) AS any_lcp,
      IS_GOOD(fast_lcp, avg_lcp, slow_lcp) AS good_lcp,
      (IS_GOOD(fast_inp, avg_inp, slow_inp) OR fast_inp IS NULL) AND IS_GOOD(small_cls, medium_cls, large_cls) AND IS_GOOD(fast_lcp, avg_lcp, slow_lcp) AS good_cwv
    FROM
      `chrome-ux-report.materialized.device_summary` AS cwvs
     JOIN
      site_on_to_date_with_feature
    ON (
      site_on_to_date_with_feature.origin = CONCAT(cwvs.origin, '/') AND
      site_on_to_date_with_feature.device = IF(cwvs.device = 'phone' OR cwvs.device = 'tablet', 'mobile', cwvs.device)
    )
    WHERE
      cwvs.date BETWEEN PARSE_DATE('%Y_%m_%d', '{from_date}') AND PARSE_DATE('%Y_%m_%d', '{to_date}' )
      AND cwvs.device IN ('desktop', 'tablet', 'phone')
      # Restrict to sites that are in both dates
      AND CONCAT(cwvs.origin, '/') IN (
        SELECT
          origin
        FROM
          sites_available_for_both_from_and_to
      )
  ),


  cwvs_by_date AS (
    SELECT
      date,
      device,
      COUNT(DISTINCT origin) AS origins,
      SAFE_DIVIDE(COUNTIF(good_cwv), COUNTIF(any_lcp AND any_cls)) AS pct_eligible_origins_with_good_cwv,
      SAFE_DIVIDE(COUNTIF(good_lcp), COUNTIF(any_lcp)) AS pct_eligible_origins_with_good_lcp,
      SAFE_DIVIDE(COUNTIF(good_cls), COUNTIF(any_cls)) AS pct_eligible_origins_with_good_cls,
      SAFE_DIVIDE(COUNTIF(good_inp), COUNTIF(any_inp)) AS pct_eligible_origins_with_good_inp
    FROM
      cwv_metrics_for_origins
    GROUP BY
      date, device
    ORDER BY
      date, device
    )
  SELECT * FROM cwvs_by_date
  """

  query_job = client.query(query)
  return query_job.result()  # Return the results of the query

# Step By Step testing

In [ ]:
generator_tag = 'speculation-rules'
after_date = '2024-06-01'
before_date = '2024-03-01'

active_sites = get_sites_with_feature_active(generator_tag, after_date)
count_active_sites = active_sites.count()
inactive_sites = get_sites_with_feature_inactive(generator_tag, after_date)
count_inactive_sites = inactive_sites.count()


In [ ]:
# Count feature active sites that were also feature active at the before date.
print(before_date)
active_at_from_date = get_active_sites_also_active_at_before_date(generator_tag, before_date, active_sites)
count_active_at_from_date = active_at_from_date.count()



In [ ]:
count_active_sites['origin']

In [ ]:
# Calculate the percentage of count_active_at_from_date (which might be 0)
# Calculate the percentage of count_active_at_from_date (which might be 0 so use safe divide)
if count_active_sites['origin'] > 0:
  percent_of_active_sites_also_active_at_from_date = (count_active_at_from_date['origin'] / count_active_sites['origin']) * 100
else:
  percent_of_active_sites_also_active_at_from_date = 0

inactive_to_active_percent = 100 - percent_of_active_sites_also_active_at_from_date;

In [ ]:
# Calculate CWV change
cwv_changes_active_sites = get_cwv_change_before_after(active_sites, before_date, after_date )
cwv_changes_inactive_sites = get_cwv_change_before_after(inactive_sites, before_date, after_date )

final_results = calculate_feature_impact(cwv_changes_active_sites, cwv_changes_inactive_sites)
final_results['feature_active_sites'] = count_active_sites['origin']
final_results['feature_inactive_sites'] = count_inactive_sites['origin']
final_results['inactive_to_active_percent'] = inactive_to_active_percent


In [ ]:
final_results

----

# Performance by Feature Queries from 2024-03-01

## Speculative Loading

In [ ]:
#@markdown ### Compare before/after
#@markdown * `before_date`: a date to analyze where the feature is not enabled
#@markdown * `after_date`: a date to analyze where the feature is enabled
#@markdown * `generator`: the generator tag indicating a feature is installed

before_date = '2024-03-01'
after_date = latest_dataset
generator_tag = 'speculation-rules'

results_sl2 = query_cwv_compare_feature_to_baseline_by_device(generator_tag, before_date, after_date)
print(results_sl2)

{'pct_good_cwv_change_mobile': '1.42%', 'pct_good_lcp_change_mobile': '1.30%', 'pct_good_cls_change_mobile': '2.19%', 'pct_good_inp_change_mobile': '0.56%', 'pct_good_cwv_change_desktop': '2.14%', 'pct_good_lcp_change_desktop': '2.37%', 'pct_good_cls_change_desktop': '1.63%', 'pct_good_inp_change_desktop': '-0.25%', 'feature_active_sites': 9091, 'feature_inactive_sites': 50000, 'also_active_at_before': '0.00%', 'before_date': '2024-03-01', 'after_date': '2024-09-01', 'generator_tag': 'speculation-rules', 'cwv_changes_active_sites': [0.0709573638372546, 0.05973671280401477, 0.03339427392262129, 0.09929041920330417, 0.05443899666326818, 0.06367646788742376, 0.02837772363253499, -0.0026272786983606577], 'cwv_changes_inactive_sites': [0.0567628587630879, 0.04675857079386847, 0.011511984996228963, 0.09365062821091052, 0.03303288698159201, 0.0399720547958603, 0.012113975978503277, -0.00013179455489875647]}


## Image Prioitizer

In [ ]:
# image-prioritizer
before_date = '2024-03-01'
after_date = latest_dataset
generator_tag = 'image-prioritizer'

results_ip2 = query_cwv_compare_feature_to_baseline_by_device(generator_tag, before_date, after_date)
print(results_ip2)

{'pct_good_cwv_change_mobile': '0.07%', 'pct_good_lcp_change_mobile': '0.24%', 'pct_good_cls_change_mobile': '1.99%', 'pct_good_inp_change_mobile': '0.58%', 'pct_good_cwv_change_desktop': '2.98%', 'pct_good_lcp_change_desktop': '1.71%', 'pct_good_cls_change_desktop': '2.74%', 'pct_good_inp_change_desktop': '-0.07%', 'feature_active_sites': 3057, 'feature_inactive_sites': 50000, 'also_active_at_before': '0.00%', 'before_date': '2024-03-01', 'after_date': '2024-09-01', 'generator_tag': 'image-prioritizer', 'cwv_changes_active_sites': [0.05372470728308859, 0.045826828366386796, 0.031917168837576115, 0.09848436113575865, 0.0579437376094758, 0.05101553940017034, 0.037424997986087116, 0.00018115942028984477], 'cwv_changes_inactive_sites': [0.05306598031955251, 0.04344795680480029, 0.012023500874824844, 0.09271561656330818, 0.028133587541988136, 0.03390036546028041, 0.01006490094309187, 0.0008955579797447211]}


## Embed Optimizer

In [ ]:
# embed-optimizer
before_date = '2024-03-01'
after_date = latest_dataset
generator_tag = 'embed-optimizer'

results_eo2 = query_cwv_compare_feature_to_baseline_by_device(generator_tag, before_date, after_date)
print(results_eo2)

{'pct_good_cwv_change_mobile': '-6.71%', 'pct_good_lcp_change_mobile': '-6.99%', 'pct_good_cls_change_mobile': '0.25%', 'pct_good_inp_change_mobile': '-0.26%', 'pct_good_cwv_change_desktop': '2.01%', 'pct_good_lcp_change_desktop': '-7.08%', 'pct_good_cls_change_desktop': '5.58%', 'pct_good_inp_change_desktop': '0.01%', 'feature_active_sites': 4908, 'feature_inactive_sites': 50000, 'also_active_at_before': '0.00%', 'before_date': '2024-03-01', 'after_date': '2024-09-01', 'generator_tag': 'embed-optimizer', 'cwv_changes_active_sites': [-0.008912738178832036, -0.017832398899997826, 0.013302035749933383, 0.0978406351757094, 0.05156835387437664, -0.030477031089655715, 0.06554045194282965, 0.0013325894195166388], 'cwv_changes_inactive_sites': [0.05813776995746334, 0.05203346729111852, 0.01076988011891955, 0.1004048888519854, 0.03146862294181668, 0.04029451169372489, 0.00971873533213996, 0.0012195856464317645]}


## Modern Images

In [ ]:
# webp-uploads
before_date = '2024-03-01'
after_date = latest_dataset
generator_tag = 'webp-uploads'

results_mi2 = query_cwv_compare_feature_to_baseline_by_device(generator_tag, before_date, after_date)
print(results_mi2)

{'pct_good_cwv_change_mobile': '1.53%', 'pct_good_lcp_change_mobile': '0.50%', 'pct_good_cls_change_mobile': '2.53%', 'pct_good_inp_change_mobile': '1.01%', 'pct_good_cwv_change_desktop': '2.67%', 'pct_good_lcp_change_desktop': '2.36%', 'pct_good_cls_change_desktop': '2.13%', 'pct_good_inp_change_desktop': '0.14%', 'feature_active_sites': 16148, 'feature_inactive_sites': 50000, 'also_active_at_before': '0.00%', 'before_date': '2024-03-01', 'after_date': '2024-09-01', 'generator_tag': 'webp-uploads', 'cwv_changes_active_sites': [0.06732568282636309, 0.0500484400843042, 0.036909719376889694, 0.1028913557761153, 0.05754036788123096, 0.06235835105115772, 0.03277655490922826, 0.001201716738197467], 'cwv_changes_inactive_sites': [0.05201159105926506, 0.04509394431000929, 0.011659601752061821, 0.09280415428856859, 0.030870589794880943, 0.038753358233235335, 0.011429699662780735, -0.00019254586873129753]}


## Image Sizes

In [ ]:
# auto-sizes
before_date = '2024-03-01'
after_date = latest_dataset
generator_tag = 'auto-sizes'

results_is2 = query_cwv_compare_feature_to_baseline_by_device(generator_tag, before_date, after_date)
print(results_is2)

{'pct_good_cwv_change_mobile': '0.95%', 'pct_good_lcp_change_mobile': '0.17%', 'pct_good_cls_change_mobile': '2.26%', 'pct_good_inp_change_mobile': '2.43%', 'pct_good_cwv_change_desktop': '2.96%', 'pct_good_lcp_change_desktop': '1.45%', 'pct_good_cls_change_desktop': '3.11%', 'pct_good_inp_change_desktop': '0.13%', 'feature_active_sites': 5633, 'feature_inactive_sites': 50000, 'also_active_at_before': '0.00%', 'before_date': '2024-03-01', 'after_date': '2024-09-01', 'generator_tag': 'auto-sizes', 'cwv_changes_active_sites': [0.06442163880919188, 0.048145394148988996, 0.0325715565983854, 0.11997871774408086, 0.06243687002187076, 0.05522724145910157, 0.041617845644969065, 0.001961164045756192], 'cwv_changes_inactive_sites': [0.054874468344218774, 0.04648435338003126, 0.009980232692361701, 0.09568983354224359, 0.032824792702341954, 0.0406943834871375, 0.01054937525763644, 0.0007026135858518856]}


## Optimization Detective plus Embed Optimizer

In [ ]:
# embed-optimizer
before_date = '2024-03-01'
after_date = latest_dataset
generator_tag = 'embed-optimizer'

results_eo2 = query_cwv_compare_feature_to_baseline_by_device_multiple(generator_tag, generator_tag2, before_date, after_date)
print(results_eo2)